# Importation des bibliothèques nécessaires

In [1]:
import pandas as pd
from pandas import ExcelWriter
import xlsxwriter
from pandas import ExcelFile
from datetime import datetime
import datetime
from datetime import timedelta
import numpy as np
import os
import statistics
from dateutil.parser import parse
import math
import calendar
from sklearn.cluster import DBSCAN
import joblib

In [2]:
# Charger le modèle à partir du fichier picklé
loaded_model = joblib.load("svm_model.pkl")

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator SVC from version 1.0.2 when using version 1.1.3. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


# Création de deux fonctions utilisables dans l'importation des données

In [3]:

def toZero(x):
    try:
        converted_value = int(x)
    except ValueError:
        converted_value = 0
    return converted_value

def findDay(date):
    day, month, year = (int(i) for i in date.split('/'))
    dayNumber = calendar.weekday(year, month, day)
    return dayNumber

def arrondir_multiple_de_5(nombre):
    multiple_de_5 = round(nombre / 5) * 5
    return multiple_de_5

def process_data(df_Fusion, seuil):
    groupe = 0
    df_Fusion['Groupe'] = 0

    for index, row in df_Fusion.iterrows():
        if index == 0:
            df_Fusion.at[index, 'Groupe'] = groupe
        else:
            diff = abs(row['Talon surconso identifie'] - df_Fusion.at[index - 1, 'Talon surconso identifie'])
            if diff <= seuil:
                df_Fusion.at[index, 'Groupe'] = groupe
            else:
                groupe += 1
                df_Fusion.at[index, 'Groupe'] = groupe

    df_simplified = df_Fusion.groupby(['Groupe', 'Début surconsommation', 'Fin surconsommation']).agg({
        'Code': 'first',  # Include the 'Code' column from the original dataframe
        'Energie': 'first',  # Include the 'Energie' column from the original dataframe
        'heure ouverture': 'first',  # Include the 'heure ouverture' column from the original dataframe
        'heure fermetur': 'first',  # Include the 'heure fermetur' column from the original dataframe
        'TalonRef': 'first',  # Include the 'TalonRef' column from the original dataframe
        'Début surconsommation': 'first',
        'Fin surconsommation': 'first',
        'Talon surconso identifie': 'mean',
        'impact': 'first',  # Include the 'impact' column from the original dataframe
        'NbrHeures': 'sum',
        'NbrNuits': 'first',  # Include the 'NbrNuits' column from the original dataframe
        'Impact conso (kWh)': 'first',  # Include the 'Impact conso (kWh)' column from the original dataframe
        '% Surconso': 'first',  # Include the '% Surconso' column from the original dataframe
        "Période d'alerte": 'first',  # Include the "Période d'alerte" column from the original dataframe
        'Pourcentage de précision': 'first'  # Include the 'Pourcentage de précision' column from the original dataframe
    }).reset_index(drop=True)

    return df_simplified

# Création de l'algorithme de machine learning personnalisé que nous allons utiliser dans la fusion des heures de surconsommation.

# Cet algorithme est un algorithme de clustering non supervisé.

# Il prend en compte la successivité des heures et une marge de surconsommation.

In [4]:
import numpy as np
from sklearn.base import BaseEstimator, ClusterMixin

class TimeMarginClustering(BaseEstimator, ClusterMixin):
    def __init__(self, time_margin=1, value_margin=20):
        self.time_margin = time_margin
        self.value_margin = value_margin
        self.labels_ = None

    def fit(self, X):
        # Sort the data based on the time column (column 0)
        sorted_indices = np.argsort(X[:, 0])
        sorted_X = X[sorted_indices]

        # Initialize variables for clustering
        cluster_labels = np.zeros(len(X), dtype=int)
        current_cluster = 0
        prev_time = sorted_X[0, 0]
        prev_value = sorted_X[0, 1]

        # Iterate over the sorted data and assign cluster labels
        for i in range(len(sorted_X)):
            time = sorted_X[i, 0]
            value = sorted_X[i, 1]

            # Check if the time difference exceeds the time margin
            time_diff = time - prev_time
            if time_diff > self.time_margin:
                current_cluster += 1

            # Check if the value difference exceeds the value margin
            value_diff = abs(value - prev_value)
            if time_diff <= self.time_margin and value_diff > self.value_margin:
                current_cluster += 1

            # Assign the cluster label
            cluster_labels[i] = current_cluster

            # Update previous time and value
            prev_time = time
            prev_value = value

        # Assign the cluster labels to the algorithm's attribute
        self.labels_ = cluster_labels
        return self

    def fit_predict(self, X):
        self.fit(X)
        return self.labels_

    def predict(self, X):
        return self.fit_predict(X)

# Importation des données.

# Prétraitement des données (nettoyage des données)

# La détection de la surconsommation pour les nuits.

# L'appel et l'application de l'algorithme de fusion des heures pour les nuits.

In [5]:
writer = pd.ExcelWriter('Suivi.xlsx', engine='xlsxwriter')

Code_list=[]
TalonRef_list=[]
Date1_list=[]
Date2_list=[]
heurev_list=[]
heuref_list=[]
NbrHeure_list=[]
defrence_list=[]
surconso_identifie=[]
Energie=[]
Marge_list=[]



# Charger les données du fichier CSV
df = pd.read_csv('data.csv', sep=',', parse_dates=True, dtype={"Date":"str","Time":"str","salesforceName":"str","siteName":"str","Real Consumption (kWh)":"int64" , "TalonRef":"int64" , "Heure Ouverture":"int64" , "Heure Fermeture":"int64" , "Ouverture dim":"str" , "Margin":"int64"},converters={'Real Consumption (kWh)':toZero},encoding="utf-8-sig")
# Filtrer les données pour l'entreprise spécifiée
#print(df.columns)
for code in df["salesforceName"].unique():
    df2 = df[df["salesforceName"] == code]

    # Sélectionner les colonnes pertinentes (Date, Time, Real Consumption (kWh) , talont , ouverture , fermeture)
    df3 = df2[['Date', 'Time', 'Real Consumption (kWh)',"TalonRef" , "Heure Ouverture" , "Heure Fermeture" , "Margin"]]

    # Convertir la colonne 'Date' en type datetime avec le format approprié
    df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')

    # Convertir la colonne 'Time' en type timedelta
    df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')

    # Combiner les colonnes 'Date' et 'Time' en une seule colonne de type datetime
    df3['DateTime'] = df3['Date'] + pd.to_timedelta(df3['Time'].dt.strftime('%H:%M:%S'))

    # Définition des heures d'ouverture et de fermeture de l'entreprise
    heure_ouverture = df3["Heure Ouverture"].iloc[0]
    heure_fermeture = df3["Heure Fermeture"].iloc[0]+1

    # Définition du talon de consommation
    talon_consommation = df3["TalonRef"].iloc[0]
    marge=df3["Margin"].iloc[0]

    # Filtrer les données pour les heures en dehors des heures d'ouverture de l'entreprise
    if heure_fermeture in [0, 1, 2]:
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= heure_fermeture) & (df3['DateTime'].dt.hour <= heure_ouverture)]
    else:
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= heure_fermeture) | (df3['DateTime'].dt.hour <= heure_ouverture)]


    # Calculer la différence entre la consommation réelle et le talon de consommation
    donnees_filtrees['Difference'] = donnees_filtrees['Real Consumption (kWh)'] - talon_consommation

    # Filtrer les heures de surconsommation (différence > talon_consommation * 0.08)
    heures_surconsommation = donnees_filtrees[donnees_filtrees['Difference'] > talon_consommation * 0.08]

    print("\n")
    print("\n")
    print("l'analyse de site : {}", code)
    print("\n")
    print("\n")

    # Liste des dates uniques dans votre DataFrame
    dates_uniques = df3['Date'].unique()

    # Parcourir chaque date et effectuer le clustering
    for i in range(len(dates_uniques) - 1):
        date_actuelle = dates_uniques[i]
        date_suivante = dates_uniques[i + 1]

        # Filtrer les données pour la date actuelle et la date suivante
        heures_nuit = heures_surconsommation[
            (heures_surconsommation['Date'] == date_actuelle) &
            (heures_surconsommation['DateTime'].dt.hour >= heure_fermeture)
        ]

        heures_nuit_suivante = heures_surconsommation[
            (heures_surconsommation['Date'] == date_suivante) &
            (heures_surconsommation['DateTime'].dt.hour <= heure_ouverture)
        ]


        # Combiner les données de la nuit actuelle et de la nuit suivante
        if heure_fermeture in [0, 1, 2]:
            heures_date = heures_nuit_suivante
        else:
            heures_date = pd.concat([heures_nuit, heures_nuit_suivante])

        #print(heures_date.head(10))

        # Convertir les colonnes de surconsommation et d'impact en tableaux Numpy
        surconsommation = heures_date['DateTime'].values.reshape(-1, 1)
        # Extraire les indices et les valeurs de la colonne "Difference" des données heures_date
        indices = heures_date.index
        differences = heures_date['Difference'].values

        # Créer le tableau NumPy à partir des indices et des valeurs
        impact = np.column_stack((indices, differences))

        print(impact)
        
        if impact.size == 0:
             continue
        else:
            # Créer l'objet DBSCAN
            clustering_algo = TimeMarginClustering(time_margin=2, value_margin=marge)


            labels = clustering_algo.fit_predict(impact)

            # Ajouter les labels de clustering comme une nouvelle colonne
            heures_date['Cluster'] = labels

            # Calculer la valeur moyenne de l'impact pour chaque cluster
            clusters_moyenne = heures_date.groupby('Cluster')['Difference'].mean().reset_index()

            # Compter le nombre d'heures regroupées dans chaque cluster
            clusters_compte = heures_date.groupby('Cluster')['DateTime'].count().reset_index()
            clusters_compte = clusters_compte.rename(columns={'DateTime': 'Nombre d\'heures regroupées'})

            # Fusionner les informations de valeur moyenne et de compte dans un seul DataFrame
            clusters_info = clusters_moyenne.merge(clusters_compte, on='Cluster')

            #saver dans un excel
            for index, row in clusters_info.iterrows():
                heuref_list.append(heure_fermeture - 1)
                Code_list.append(code)
                Energie.append('Electricité')
                TalonRef_list.append(talon_consommation)
                date1 = dates_uniques[i].to_pydatetime().date()
                #date1 = datetime.datetime.strptime(date1, '%Y-%m-%d').date()
                Date1_list.append(date1)
                date2 = dates_uniques[i + 1].to_pydatetime().date()
                #date2 = datetime.datetime.strptime(date2, '%Y-%m-%d').date()
                Date2_list.append(date2)
                heurev_list.append(heure_ouverture)
                NbrHeure_list.append(row['Nombre d\'heures regroupées'])
                defrence_list.append(int(row['Difference']))
                surconso_identifie.append(talon_consommation+int(row['Difference']))
                Marge_list.append(marge)

            # Afficher les informations des clusters pour la date spécifique
            print("\n")
            print(f"Date: {dates_uniques[i]}")
            print("\n")
            print(clusters_info)
            print("\n")
          

df_NuitOut = pd.DataFrame({'Code':Code_list, 'Energie': Energie,'heure ouverture':heurev_list,'heure fermetur':heuref_list, 'TalonRef':TalonRef_list, 'Début surconsommation':Date1_list, 'Fin surconsommation':Date2_list, 'Talon surconso identifie':surconso_identifie, 'impact':defrence_list,'NbrHeures':NbrHeure_list, 'Marge':Marge_list})

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:18: ParserWarning: Both a converter and dtype were specified for column Real Consumption (kWh) - only the converter will be used.
  df = pd.read_csv('S4.csv', sep=',', parse_dates=True, dtype={"Date":"str","Time":"str","salesforceName":"str","siteName":"str","Real Consumption (kWh)":"int64" , "TalonRef":"int64" , "Heure Ouverture":"int64" , "Heure Fermeture":"int64" , "Ouverture dim":"str" , "Margin":"int64"},converters={'Real Consumption (kWh)':toZero},encoding="utf-8-sig")
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\





l'analyse de site : {} CS467




[]
[]
[]
[]
[]
[]
[]




l'analyse de site : {} CS531




[[214  15]
 [215   9]
 [216  13]
 [217  16]
 [218  11]
 [219  13]
 [220  13]]


Date: 2024-01-21 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        15.0                           1
1        1        12.5                           6


[[238  16]
 [239  11]
 [240  13]
 [241  14]
 [242  16]
 [243  15]
 [244  14]]


Date: 2024-01-22 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0   14.142857                           7


[[262  16]
 [263  12]
 [264  15]
 [265  15]
 [266  14]
 [267  18]
 [268  16]]


Date: 2024-01-23 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0   15.142857                           7


[[286  22]
 [287  16]
 [288  17]
 [289  17]
 [290  17]
 [291  19]
 [292  20]]


Date: 2024-01-24 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0   22.000000                           1
1       

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFra





l'analyse de site : {} CS404




[[984  17]
 [985  17]
 [986  17]
 [987  20]
 [988  18]]


Date: 2024-01-21 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        17.8                           5


[[1011    5]
 [1012    3]]


Date: 2024-01-22 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         4.0                           2


[[1032    3]
 [1033    3]
 [1034    3]
 [1035    5]
 [1036    4]]


Date: 2024-01-23 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         3.6                           5


[[1059    4]
 [1060    3]]


Date: 2024-01-24 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         3.5                           2


[[1080    3]
 [1081    3]
 [1083    5]
 [1084    3]]


Date: 2024-01-25 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         3.5                           4


[[1107    5]
 [1108    3]]


Date: 2024-01-26 00:00:00


   Clus

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFra

...

[]
[]




l'analyse de site : {} MP3443




[[111534      1]
 [111537      1]
 [111538      1]
 [111539      2]
 [111540      1]
 [111541      1]]


Date: 2024-01-21 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         1.0                           1
1        1         1.2                           5


[[111558      2]
 [111559      1]
 [111560      1]
 [111561      1]
 [111562      2]
 [111563      2]
 [111564      3]
 [111565      4]]


Date: 2024-01-22 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         2.0                           8


[[111582      1]
 [111584      1]
 [111587      1]
 [111588      1]
 [111589      3]]


Date: 2024-01-23 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0    1.000000                           2
1        1    1.666667                           3


[[111606      1]
 [111608      1]
 [111611      1]
 [111612      1]
 [111613      4]]


Date: 2024-01-24 00:00:00


   Cluster

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFra



Date: 2024-01-23 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         7.5                           2
1        1        25.0                           2


[[111803     10]
 [111804     27]
 [111805     17]]


Date: 2024-01-24 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        10.0                           1
1        1        22.0                           2


[[111827      9]
 [111828     18]
 [111829     12]]


Date: 2024-01-25 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        13.0                           3


[[111850      7]
 [111851      9]
 [111852     30]
 [111853     19]]


Date: 2024-01-26 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         8.0                           2
1        1        24.5                           2


[[111875      6]
 [111876     27]
 [111877     13]]


Date: 2024-01-27 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0    

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\471266531.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFra

   Cluster  Difference  Nombre d'heures regroupées
0        0         1.0                           1


[[112164      3]]


Date: 2024-01-23 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         3.0                           1


[[112188      2]]


Date: 2024-01-24 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         2.0                           1


[[112212      3]]


Date: 2024-01-25 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         3.0                           1


[[112236      1]]


Date: 2024-01-26 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         1.0                           1


[]


# La détection de la surconsommation pour les dimanches.

# L'appel et l'application de l'algorithme de fusion des heures pour les dimanches.

# L'organisation des sorties dans une feuille d'un fichier Excel.

In [6]:
dCode_list=[]
dTalonRef_list=[]
dDate1_list=[]
dDate2_list=[]
dheurev_list=[]
dheuref_list=[]
dNbrHeure_list=[]
ddefrence_list=[]
dsurconso_identifie=[]
dEnergie=[]
dNbrNuit=[]
Impact_conso = []
perSurconso = []
Periode = []


# Convert 'Date' column to datetime type if needed
df['Date'] = pd.to_datetime(df['Date'])

# Filter the data to keep only Sundays
sundays_data = df[df['Date'].dt.weekday == 6]

# Print the filtered data
#print(sundays_data.head(30))
df = sundays_data
for code in df["salesforceName"].unique():
    df2 = df[df["salesforceName"] == code]

    # Select relevant columns: Date, Time, Real Consumption (kWh), TalonRef, Heure Ouverture, Heure Fermeture, Ouverture dim
    df3 = df2[['Date', 'Time', 'Real Consumption (kWh)', 'TalonRef', 'Heure Ouverture', 'Heure Fermeture', 'Ouverture dim' , 'Margin']]

    # Convert the 'Date' column to datetime type with the appropriate format
    df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')

    # Convert the 'Time' column to timedelta type
    df3['Time'] = pd.to_timedelta(df3['Time'])

    # Combine the 'Date' and 'Time' columns into a single datetime column
    df3['DateTime'] = df3['Date'] + df3['Time']

    # Define the opening and closing hours of the company
    heure_ouverture = df3["Heure Ouverture"].iloc[0]
    heure_fermeture = df3["Heure Fermeture"].iloc[0] + 1
    ouverture_dim = df3["Ouverture dim"].iloc[0]

    # Define the consumption threshold
    talon_consommation = df3["TalonRef"].iloc[0]
    marge=df3["Margin"].iloc[0]

    # Filter the data for hours outside the company's opening hours
    if ouverture_dim == "Journée":
        donnees_filtrees = pd.DataFrame()
    elif ouverture_dim == "Fermé":
        donnees_filtrees = df3[(df3['DateTime'].dt.hour > heure_ouverture) & (df3['DateTime'].dt.hour < heure_fermeture)]
    elif ouverture_dim == "Matin":
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= 14) & (df3['DateTime'].dt.hour < heure_fermeture)]

    if len(donnees_filtrees) > 0:
        # Calculate the difference between the actual consumption and the consumption threshold
        donnees_filtrees['Difference'] = donnees_filtrees['Real Consumption (kWh)'] - talon_consommation

        # Filter the overconsumption hours (difference > talon_consommation * 0.08)
        heures_surconsommation = donnees_filtrees[donnees_filtrees['Difference'] > talon_consommation * 0.08]

        # Print the hours of overconsumption
        if len(heures_surconsommation) > 0:
            print(heures_surconsommation)

        print("\n")
        print("\n")
        print("l'analyse de site : {}", code)
        print("\n")
        print("\n")

        print(len(heures_surconsommation))

        # Liste des dates uniques dans votre DataFrame
        dates_uniques = heures_surconsommation['Date'].unique()
        
        # Parcourir chaque date et effectuer le clustering
        for i in range(len(dates_uniques)-1):
            date = dates_uniques[i+1]

            heures_date = heures_surconsommation[(heures_surconsommation['Date'] == date)]
            #print(heures_date.head(10))

            # Convertir les colonnes de surconsommation et d'impact en tableaux Numpy
            surconsommation = heures_date['DateTime'].values.reshape(-1, 1)
            # Extraire les indices et les valeurs de la colonne "Difference" des données heures_date
            indices = heures_date.index
            differences = heures_date['Difference'].values

            # Créer le tableau NumPy à partir des indices et des valeurs
            impact = np.column_stack((indices, differences))

            
            # Créer l'objet DBSCAN
            clustering_algo = TimeMarginClustering(time_margin=2, value_margin=marge)

            labels = clustering_algo.fit_predict(impact)

            # Ajouter les labels de clustering comme une nouvelle colonne
            heures_date['Cluster'] = labels

            # Calculer la valeur moyenne de l'impact pour chaque cluster
            clusters_moyenne = heures_date.groupby('Cluster')['Difference'].mean().reset_index()

            # Compter le nombre d'heures regroupées dans chaque cluster
            clusters_compte = heures_date.groupby('Cluster')['DateTime'].count().reset_index()
            clusters_compte = clusters_compte.rename(columns={'DateTime': 'Nombre d\'heures regroupées'})

            # Fusionner les informations de valeur moyenne et de compte dans un seul DataFrame
            clusters_info = clusters_moyenne.merge(clusters_compte, on='Cluster')

            #saver dans un excel
            for index, row in clusters_info.iterrows():
                dheuref_list.append(heure_fermeture - 1)
                dCode_list.append(code)
                dEnergie.append('Electricité')
                dTalonRef_list.append(talon_consommation)
                date1 = dates_uniques[i+1].to_pydatetime().date()
                dDate1_list.append(date1)
               # date_string = np.datetime_as_string(dates_uniques[i+1], unit='D')
                #date2 = datetime.datetime.strptime(date_string, '%Y-%m-%d').date()
                dDate2_list.append(date1)
                dheurev_list.append(heure_ouverture)
                dNbrHeure_list.append(row['Nombre d\'heures regroupées'])
                ddefrence_list.append(int(row['Difference']))
                dsurconso_identifie.append(arrondir_multiple_de_5(talon_consommation+int(row['Difference'])))
                surconso = row['Nombre d\'heures regroupées'] * int(row['Difference'])
                dNbrNuit.append(1)
                Impact_conso.append(surconso)

                persurconso = (int(row['Difference']) /  talon_consommation)*100
                persurconso = int(persurconso)
                persurconso = str(persurconso)
                persurconso = persurconso + '%'
                perSurconso.append(persurconso)
                Periode.append('Dim')

df_dimOut = pd.DataFrame({'Code':dCode_list, 'Energie': dEnergie,'heure ouverture':dheurev_list,'heure fermetur':dheuref_list, 'TalonRef':dTalonRef_list, 'Début surconsommation':dDate1_list, 'Fin surconsommation':dDate2_list, 'Talon surconso identifie':dsurconso_identifie, 'impact':ddefrence_list,'NbrHeures':dNbrHeure_list, 'NbrNuits':dNbrNuit, 'Impact conso (kWh)':Impact_conso, '% Surconso':perSurconso, "Période d'alerte":Periode})
grouped_df = df_dimOut.groupby("Code").size().reset_index(name="Nombre de lignes")
grouped_df["Pourcentage de précision"] = 100 - (grouped_df["Nombre de lignes"] - 1) * 10
df = df_dimOut.merge(grouped_df[["Code", "Pourcentage de précision"]], on="Code", how="left")
df['Pourcentage de précision'] = df['Pourcentage de précision'].astype(str) + '%'
df = process_data(df , 5)

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

          Date            Time  Real Consumption (kWh)  TalonRef  \
197 2024-01-21 0 days 05:00:00                      56        45   
198 2024-01-21 0 days 06:00:00                      64        45   
199 2024-01-21 0 days 07:00:00                      60        45   
200 2024-01-21 0 days 08:00:00                      60        45   
201 2024-01-21 0 days 09:00:00                      60        45   
202 2024-01-21 0 days 10:00:00                      58        45   
203 2024-01-21 0 days 11:00:00                      58        45   
204 2024-01-21 0 days 12:00:00                      62        45   
205 2024-01-21 0 days 13:00:00                      59        45   
206 2024-01-21 0 days 14:00:00                      61        45   
207 2024-01-21 0 days 15:00:00                      61        45   
208 2024-01-21 0 days 16:00:00                      58        45   
209 2024-01-21 0 days 17:00:00                      60        45   
210 2024-01-21 0 days 18:00:00                  

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

           Date            Time  Real Consumption (kWh)  TalonRef  \
1541 2024-01-21 0 days 05:00:00                      50        45   
1542 2024-01-21 0 days 06:00:00                      54        45   
1543 2024-01-21 0 days 07:00:00                     112        45   
1544 2024-01-21 0 days 08:00:00                     113        45   
1545 2024-01-21 0 days 09:00:00                     110        45   
1546 2024-01-21 0 days 10:00:00                     114        45   
1547 2024-01-21 0 days 11:00:00                     114        45   
1548 2024-01-21 0 days 12:00:00                      98        45   
1549 2024-01-21 0 days 13:00:00                      86        45   
1550 2024-01-21 0 days 14:00:00                      88        45   
1551 2024-01-21 0 days 15:00:00                      87        45   
1552 2024-01-21 0 days 16:00:00                      87        45   
1553 2024-01-21 0 days 17:00:00                      90        45   
1554 2024-01-21 0 days 18:00:00   

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

...

             Date            Time  Real Consumption (kWh)  TalonRef  \
106886 2024-01-21 0 days 14:00:00                     145        80   
106887 2024-01-21 0 days 15:00:00                     146        80   
106888 2024-01-21 0 days 16:00:00                     148        80   
106889 2024-01-21 0 days 17:00:00                     147        80   
106890 2024-01-21 0 days 18:00:00                     146        80   
106891 2024-01-21 0 days 19:00:00                     143        80   
106892 2024-01-21 0 days 20:00:00                      99        80   
107054 2024-01-28 0 days 14:00:00                     153        80   
107055 2024-01-28 0 days 15:00:00                     148        80   
107056 2024-01-28 0 days 16:00:00                     147        80   
107057 2024-01-28 0 days 17:00:00                     147        80   
107058 2024-01-28 0 days 18:00:00                     148        80   
107059 2024-01-28 0 days 19:00:00                     146        80   
107060

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

             Date            Time  Real Consumption (kWh)  TalonRef  \
109135 2024-01-21 0 days 14:00:00                      46        20   
109136 2024-01-21 0 days 15:00:00                      45        20   
109137 2024-01-21 0 days 16:00:00                      47        20   
109138 2024-01-21 0 days 17:00:00                      47        20   
109139 2024-01-21 0 days 18:00:00                      45        20   
109140 2024-01-21 0 days 19:00:00                      45        20   
109141 2024-01-21 0 days 20:00:00                      36        20   
109142 2024-01-21 0 days 21:00:00                      36        20   
109303 2024-01-28 0 days 14:00:00                      51        20   
109304 2024-01-28 0 days 15:00:00                      50        20   
109305 2024-01-28 0 days 16:00:00                      49        20   
109306 2024-01-28 0 days 17:00:00                      49        20   
109307 2024-01-28 0 days 18:00:00                      49        20   
109308

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\561942071.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc

             Date            Time  Real Consumption (kWh)  TalonRef  \
111338 2024-01-21 0 days 18:00:00                     112       100   
111339 2024-01-21 0 days 19:00:00                     117       100   
111340 2024-01-21 0 days 20:00:00                     117       100   
111502 2024-01-28 0 days 14:00:00                     110       100   
111506 2024-01-28 0 days 18:00:00                     112       100   
111507 2024-01-28 0 days 19:00:00                     113       100   
111508 2024-01-28 0 days 20:00:00                     112       100   

        Heure Ouverture  Heure Fermeture Ouverture dim  Margin  \
111338                4               23         Matin       5   
111339                4               23         Matin       5   
111340                4               23         Matin       5   
111502                4               23         Matin       5   
111506                4               23         Matin       5   
111507                4            

# Prétraitement des données et appel du modèle de machine learning (Random Forest) pour dimanches.

In [7]:
data = df[["Talon surconso identifie", "impact", "NbrHeures", "NbrNuits", "Impact conso (kWh)", "% Surconso", "Période d'alerte"]]
data.head()

Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                     66.25      19       17.0         1               209.0   
1                    110.00      42        6.0         1               252.0   
2                    100.00      30        4.0         1               120.0   
3                    110.00      48        7.0         1               336.0   
4                    100.00      41        2.0         1                82.0   

  % Surconso Période d'alerte  
0        42%              Dim  
1        60%              Dim  
2        42%              Dim  
3        80%              Dim  
4        68%              Dim

In [8]:
print(data.dtypes)

Talon surconso identifie    float64
impact                        int64
NbrHeures                   float64
NbrNuits                      int64
Impact conso (kWh)          float64
% Surconso                   object
Période d'alerte             object
dtype: object


In [9]:
# Transformation de la colonne '% Surconso' en float
data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)

# Affichage du dataframe après la transformation
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\3833681290.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                     66.25      19       17.0         1               209.0   
1                    110.00      42        6.0         1               252.0   
2                    100.00      30        4.0         1               120.0   
3                    110.00      48        7.0         1               336.0   
4                    100.00      41        2.0         1                82.0   

   % Surconso Période d'alerte  
0        0.42              Dim  
1        0.60              Dim  
2        0.42              Dim  
3        0.80              Dim  
4        0.68              Dim

In [10]:
# Créer un dictionnaire de mapping
mapping = {"Nuit": 0, "Dim": 1, "Jour": 2, "Jour/nuit": 3, "Jour/Nuit": 3}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)

# Afficher les 5 premières lignes du DataFrame
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\3671493290.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                     66.25      19       17.0         1               209.0   
1                    110.00      42        6.0         1               252.0   
2                    100.00      30        4.0         1               120.0   
3                    110.00      48        7.0         1               336.0   
4                    100.00      41        2.0         1                82.0   

   % Surconso  Période d'alerte  
0        0.42                 1  
1        0.60                 1  
2        0.42                 1  
3        0.80                 1  
4        0.68                 1

In [11]:
# Faire des prédictions pour chaque ligne de la dataframe
predictions = loaded_model.predict(data)
df["Catégorie"] = predictions
# Créer un dictionnaire de mapping
mapping = {0: "Investigation en cours", 1: "Changement de comportement", 2: "Eclairage", 3: "Froid", 4: "CVC", 5:"Multi-usage"}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
df['Catégorie'] = df['Catégorie'].replace(mapping)
df.head(15)

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- NbrHeures
- NbrNuits
- Talon surconso identifie
- impact
Feature names seen at fit time, yet now missing:
- DP Surconso (kW)
- Nb d'heures
- Nb nuits/jours concernés
- Talon surconso identifié

  warnings.warn(message, FutureWarning)


Code      Energie  heure ouverture  heure fermetur  TalonRef  \
0    CS531  Electricité                4              20        45   
1   MO0160  Electricité                5              23        70   
2   MO0160  Electricité                5              23        70   
3   MO1244  Electricité                5              21        60   
4   MO1244  Electricité                5              21        60   
5    CS404  Electricité                4              22        35   
6   MO2147  Electricité                5              20        30   
7    CS271  Electricité                4              22        45   
8    CS271  Electricité                4              22        45   
9    CS271  Electricité                4              22        45   
10   CS271  Electricité                4              22        45   
11   CS271  Electricité                4              22        45   
12   CS271  Electricité                4              22        45   
13   CS271  Electricité                4              22        45   
14   CS271  Electricité                4              22        45   

   Début surconsommation Fin surconsommation  Talon surconso identifie  \
0             2024-01-28          2024-01-28                 66.250000   
1             2024-01-28          2024-01-28                110.000000   
2             2024-01-28          2024-01-28                100.000000   
3             2024-01-28          2024-01-28                110.000000   
4             2024-01-28          2024-01-28                100.000000   
5             2024-01-28          2024-01-28                 40.000000   
6             2024-01-28          2024-01-28                 50.000000   
7             2024-01-28          2024-01-28                 72.500000   
8             2024-01-28          2024-01-28                130.000000   
9             2024-01-28          2024-01-28                100.000000   
10            2024-01-28          2024-01-28                 76.666667   
11            2024-01-28          2024-01-28                 95.000000   
12            2024-01-28          2024-01-28                105.000000   
13            2024-01-28          2024-01-28                 95.000000   
14            2024-01-28          2024-01-28                 72.500000   

    impact  NbrHeures  NbrNuits  Impact conso (kWh) % Surconso  \
0       19       17.0         1               209.0        42%   
1       42        6.0         1               252.0        60%   
2       30        4.0         1               120.0        42%   
3       48        7.0         1               336.0        80%   
4       41        2.0         1                82.0        68%   
5        4        2.0         1                 8.0        11%   
6       19        8.0         1               152.0        63%   
7       25        2.0         1                25.0        55%   
8       84        1.0         1                84.0       186%   
9       56        4.0         1               224.0       124%   
10      30        5.0         1                90.0        66%   
11      48        1.0         1                48.0       106%   
12      59        1.0         1                59.0       131%   
13      50        1.0         1                50.0       111%   
14      23        5.0         1                92.0        51%   

   Période d'alerte Pourcentage de précision                   Catégorie  
0               Dim                      70%  Changement de comportement  
1               Dim                      90%  Changement de comportement  
2               Dim                      90%  Changement de comportement  
3               Dim                      90%  Changement de comportement  
4               Dim                      90%  Changement de comportement  
5               Dim                     100%                         CVC  
6               Dim                     100%                         CVC  
7               Dim                       0

In [12]:
df.to_excel(writer, sheet_name='dim', index=False)

# Création de l'algorithme de machine learning personnalisé que nous allons utiliser dans la fusion des nuits de surconsommation.

# Il prend en compte la successivité des dates, une marge de surconsommation et une marge des heures.

In [13]:
def custom_clustering(X, date_margin, consumption_margin, hours_margin, cond):
    clusters = []
    remaining_points = X.copy()

    while len(remaining_points) > 0:
        current_point = remaining_points[0]
        cluster = [current_point]
        remaining_points = np.delete(remaining_points, 0, axis=0)
        i = 0

        # Sauvegarde de la valeur originale de date_margin
        original_date_margin = date_margin

        while i < len(remaining_points):
            point = remaining_points[i]


            if (abs(point[0] - current_point[0]) <= date_margin and
                abs(point[1] - current_point[1]) <= consumption_margin and
                abs(point[2] - current_point[2]) <= hours_margin):

                current_point = point
                cluster.append(point)
                remaining_points = np.delete(remaining_points, i, axis=0)
            else:
                i += 1

            # Vérification de la condition et mise à jour de date_margin si nécessaire
            if point[2] >= cond:
                date_margin = 1

        # Rétablissement de la valeur originale de date_margin
        date_margin = original_date_margin

        clusters.append(cluster)

    return clusters
def create_cluster_dataframe(clusters):
    cluster_data=[]
    for cluster in clusters:
        consomption_mean = np.mean([point[1] for point in cluster])
        hours_mean = np.mean([point[2] for point in cluster])
        count = len(cluster)
        cluster_data.append([consomption_mean ,hours_mean , count])
    df = pd.DataFrame(cluster_data, columns=['Mean Consomption' , 'Mean Hours', 'Count'])
    return df

# L'appel et l'application de l'algorithme de fusion des nuits sur les données output de fusion des heures pour les nuits.

In [14]:
Code_list=[]
TalonRef_list=[]
Date1_list=[]
Date2_list=[]
heurev_list=[]
heuref_list=[]
NbrHeure_list=[]
defrence_list=[]
surconso_identifie=[]
Energie=[]
NbrNuit_list=[]
NImpact_conso = []
NperSurconso = []
NPeriode = []



for code in df_NuitOut["Code"].unique():
    df_Nuit = df_NuitOut[df_NuitOut["Code"] == code]
    # Votre code précédent ici...

    # Créer un tableau Numpy à partir des colonnes spécifiées
    X = np.column_stack((df_Nuit.index, df_Nuit['Talon surconso identifie'], df_Nuit['NbrHeures']))

    print(X)
    cond = (23 - df_Nuit['heure fermetur'].iloc[0])+df_Nuit['heure ouverture'].iloc[0]
    marge=df_Nuit['Marge'].iloc[0]
   
    clusters = custom_clustering(X , date_margin=2 , consumption_margin=marge , hours_margin=2 , cond=cond)
    
    df = create_cluster_dataframe(clusters)
    print(df.head(5))

    for (index, row), cluster in zip(df.iterrows(), clusters):
        Energie.append('Electricité')
        heuref_list.append(df_Nuit['heure fermetur'].iloc[0])
        Code_list.append(code)
        TalonRef_list.append(df_Nuit['TalonRef'].iloc[0])
        first_index = int(cluster[0][0])
        Date1_list.append(df_NuitOut['Début surconsommation'].iloc[first_index])
        last_index = int(cluster[-1][0])
        Date2_list.append(df_NuitOut['Fin surconsommation'].iloc[last_index])
        heurev_list.append(df_Nuit['heure ouverture'].iloc[0])
        surconso_identifie.append(arrondir_multiple_de_5(int(row['Mean Consomption'])))
        defrence_list.append(int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0])
        NbrHeure_list.append(round(row['Mean Hours']))
        NbrNuit_list.append(row['Count'])
        surconso = round(row['Mean Hours']) * (int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0]) * row['Count']
        NImpact_conso.append(surconso)

        persurconso = ((int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0]) /  df_Nuit['TalonRef'].iloc[0])*100
        persurconso = int(persurconso)
        persurconso = str(persurconso)
        persurconso = persurconso + '%'
        NperSurconso.append(persurconso)
        NPeriode.append('Nuit')

df_Fusion = pd.DataFrame({'Code':Code_list, 'Energie': Energie,'heure ouverture':heurev_list,'heure fermetur':heuref_list, 'TalonRef':TalonRef_list, 'Début surconsommation':Date1_list, 'Fin surconsommation':Date2_list, 'Talon surconso identifie':surconso_identifie, 'impact':defrence_list,'NbrHeures':NbrHeure_list, 'NbrNuits':NbrNuit_list, 'Impact conso (kWh)':NImpact_conso, '% Surconso':NperSurconso, "Période d'alerte":NPeriode})
grouped_df = df_Fusion.groupby("Code").size().reset_index(name="Nombre de lignes")
grouped_df["Pourcentage de précision"] = np.maximum(30, 100 - (grouped_df["Nombre de lignes"] - 1) * 10)
df = df_Fusion.merge(grouped_df[["Code", "Pourcentage de précision"]], on="Code", how="left")
df['Pourcentage de précision'] = df['Pourcentage de précision'].astype(str) + '%'
df = process_data(df , 5)

[[ 0. 60.  1.]
 [ 1. 57.  6.]
 [ 2. 59.  7.]
 [ 3. 60.  7.]
 [ 4. 67.  1.]
 [ 5. 62.  6.]
 [ 6. 60.  7.]
 [ 7. 61.  7.]
 [ 8. 61.  7.]]
   Mean Consomption  Mean Hours  Count
0         60.000000    1.000000      1
1         58.666667    6.666667      3
2         67.000000    1.000000      1
3         61.000000    6.750000      4
[[  9. 119.   6.]
 [ 10. 119.   6.]
 [ 11. 105.   6.]
 [ 12.  92.   2.]
 [ 13.  79.   2.]
 [ 14.  91.   2.]
 [ 15.  88.   6.]
 [ 16. 103.   6.]]
   Mean Consomption  Mean Hours  Count
0             119.0         6.0      2
1             105.0         6.0      1
2              91.5         2.0      2
3              79.0         2.0      1
4              88.0         6.0      1
[[ 17.  82.   1.]
 [ 18.  72.   6.]
 [ 19.  99.   1.]
 [ 20. 102.   3.]
 [ 21.  91.   1.]
 [ 22.  90.   1.]
 [ 23.  91.   1.]
 [ 24.  89.   1.]]
   Mean Consomption  Mean Hours  Count
0             82.00         1.0      1
1             72.00         6.0      1
2            100.50         

[[324.  66.   2.]
 [325.  75.   1.]
 [326.  73.   1.]
 [327.  74.   1.]
 [328.  73.   1.]
 [329.  73.   1.]
 [330.  70.   1.]
 [331.  78.   1.]]
   Mean Consomption  Mean Hours  Count
0              66.0         2.0      1
1              73.0         1.0      6
2              78.0         1.0      1
[[332. 131.   2.]
 [333. 130.   2.]
 [334. 135.   2.]
 [335. 124.   1.]
 [336. 149.   1.]
 [337. 141.   2.]
 [338. 136.   2.]
 [339. 145.   2.]
 [340. 137.   2.]
 [341. 143.   2.]
 [342. 133.   2.]
 [343. 139.   2.]
 [344. 136.   2.]
 [345. 136.   2.]
 [346. 119.   1.]
 [347. 144.   1.]]
   Mean Consomption  Mean Hours  Count
0        134.642857    1.857143     14
1        149.000000    1.000000      1
2        144.000000    1.000000      1
[[348.  20.   3.]
 [349.  14.   3.]
 [350.  14.   3.]
 [351.  14.   3.]
 [352.  15.   2.]
 [353.  20.   2.]]
   Mean Consomption  Mean Hours  Count
0         16.166667    2.666667      6
[[354. 215.   1.]
 [355. 281.   1.]
 [356. 207.   1.]
 [357. 269.  

[[662.  80.   1.]
 [663.  74.   1.]
 [664.  86.   1.]
 [665.  77.   1.]
 [666.  88.   1.]
 [667.  80.   1.]
 [668.  74.   2.]
 [669.  89.   1.]
 [670.  72.   1.]
 [671.  67.   3.]
 [672.  77.   1.]
 [673.  71.   1.]
 [674.  62.   3.]
 [675.  73.   1.]
 [676.  67.   1.]
 [677.  63.   3.]
 [678.  73.   1.]
 [679.  67.   1.]
 [680.  86.   1.]
 [681.  73.   1.]
 [682.  90.   2.]
 [683.  98.   1.]
 [684.  92.   4.]
 [685.  99.   1.]]
   Mean Consomption  Mean Hours  Count
0              80.0         1.0      1
1              77.0         1.0      3
2              87.0         1.0      2
3              71.4         1.6      5
4              89.0         1.0      1
[[686.  58.   2.]
 [687.  55.   1.]
 [688.  57.   2.]
 [689.  58.   2.]
 [690.  56.   2.]
 [691.  56.   2.]
 [692.  57.   1.]
 [693.  57.   1.]]
   Mean Consomption  Mean Hours  Count
0             56.75       1.625      8
[[694.  34.   2.]
 [695.  39.   5.]
 [696.  55.   5.]
 [697.  55.   5.]
 [698.  55.   5.]
 [699.  39.   5.]
 [

[[1.058e+03 8.300e+01 1.000e+00]
 [1.059e+03 8.600e+01 1.000e+00]
 [1.060e+03 9.300e+01 1.000e+00]
 [1.061e+03 6.700e+01 2.000e+00]
 [1.062e+03 6.700e+01 1.000e+00]
 [1.063e+03 8.600e+01 1.000e+00]
 [1.064e+03 8.800e+01 1.000e+00]
 [1.065e+03 8.500e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0         84.500000         1.0      2
1         93.000000         1.0      1
2         67.000000         1.5      2
3         86.333333         1.0      3
[[1.066e+03 6.000e+01 1.000e+00]
 [1.067e+03 6.000e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0              60.0         1.0      2
[[1.068e+03 6.800e+01 2.000e+00]
 [1.069e+03 7.400e+01 1.000e+00]
 [1.070e+03 6.100e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0              68.0         2.0      1
1              74.0         1.0      1
2              61.0         1.0      1
[[1.071e+03 7.200e+01 4.000e+00]
 [1.072e+03 8.200e+01 1.000e+00]
 [1.073e+03 6.500e+01 3.000e+00]
 [1.074e+03 7.500e+01 1.000e+00]
 [1.075

[[1267.  284.    7.]
 [1268.  281.    7.]
 [1269.  227.    7.]
 [1270.  280.    7.]
 [1271.  277.    7.]
 [1272.  274.    7.]
 [1273.  277.    7.]]
   Mean Consomption  Mean Hours  Count
0             282.5         7.0      2
1             227.0         7.0      1
2             277.0         7.0      4
[[1.274e+03 8.000e+01 2.000e+00]
 [1.275e+03 6.300e+01 5.000e+00]
 [1.276e+03 7.900e+01 2.000e+00]
 [1.277e+03 6.200e+01 5.000e+00]
 [1.278e+03 7.900e+01 2.000e+00]
 [1.279e+03 6.200e+01 4.000e+00]
 [1.280e+03 7.600e+01 2.000e+00]
 [1.281e+03 6.000e+01 4.000e+00]
 [1.282e+03 8.000e+01 2.000e+00]
 [1.283e+03 6.200e+01 5.000e+00]
 [1.284e+03 7.900e+01 2.000e+00]
 [1.285e+03 6.200e+01 5.000e+00]
 [1.286e+03 7.900e+01 2.000e+00]
 [1.287e+03 6.000e+01 1.000e+00]
 [1.288e+03 6.300e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0         78.857143    2.000000      7
1         61.833333    4.666667      6
2         61.500000    1.000000      2
[[1289.   33.    5.]
 [1290.   34.    5.]
 [

...

[[3.551e+03 1.280e+02 1.000e+00]
 [3.552e+03 1.360e+02 1.000e+00]
 [3.553e+03 1.320e+02 2.000e+00]
 [3.554e+03 1.270e+02 1.000e+00]
 [3.555e+03 1.300e+02 1.000e+00]
 [3.556e+03 1.360e+02 1.000e+00]
 [3.557e+03 1.300e+02 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0             129.4         1.2      5
1             136.0         1.0      1
2             136.0         1.0      1
[[3.558e+03 9.600e+01 3.000e+00]
 [3.559e+03 9.000e+01 2.000e+00]
 [3.560e+03 1.020e+02 1.000e+00]
 [3.561e+03 9.800e+01 3.000e+00]
 [3.562e+03 9.600e+01 3.000e+00]
 [3.563e+03 9.500e+01 3.000e+00]
 [3.564e+03 9.300e+01 2.000e+00]
 [3.565e+03 1.030e+02 1.000e+00]
 [3.566e+03 9.700e+01 3.000e+00]]
   Mean Consomption  Mean Hours  Count
0              96.0         2.5      8
1             102.0         1.0      1
[[3567.   82.    7.]
 [3568.   76.    7.]
 [3569.   78.    7.]
 [3570.   77.    7.]
 [3571.   77.    7.]
 [3572.   77.    7.]
 [3573.   76.    7.]]
   Mean Consomption  Mean Hours  Count
0         

[[3.812e+03 4.900e+01 6.000e+00]
 [3.813e+03 6.300e+01 1.000e+00]
 [3.814e+03 4.000e+01 7.000e+00]
 [3.815e+03 4.900e+01 7.000e+00]
 [3.816e+03 4.900e+01 7.000e+00]
 [3.817e+03 4.700e+01 7.000e+00]]
   Mean Consomption  Mean Hours  Count
0         49.000000         6.0      1
1         63.000000         1.0      1
2         40.000000         7.0      1
3         48.333333         7.0      3
[[3.818e+03 1.700e+01 1.000e+00]
 [3.819e+03 3.200e+01 1.000e+00]
 [3.820e+03 1.700e+01 2.000e+00]
 [3.821e+03 3.500e+01 1.000e+00]
 [3.822e+03 1.700e+01 3.000e+00]
 [3.823e+03 3.400e+01 1.000e+00]
 [3.824e+03 1.700e+01 3.000e+00]
 [3.825e+03 3.300e+01 1.000e+00]
 [3.826e+03 1.700e+01 4.000e+00]
 [3.827e+03 4.200e+01 1.000e+00]
 [3.828e+03 2.100e+01 7.000e+00]
 [3.829e+03 4.200e+01 1.000e+00]
 [3.830e+03 1.700e+01 2.000e+00]]
   Mean Consomption  Mean Hours  Count
0         17.000000         2.6      5
1         36.333333         1.0      6
2         21.000000         7.0      1
3         17.000000 

[[4.032e+03 3.500e+02 1.000e+00]
 [4.033e+03 3.380e+02 4.000e+00]
 [4.034e+03 3.780e+02 1.000e+00]
 [4.035e+03 3.270e+02 5.000e+00]
 [4.036e+03 3.620e+02 1.000e+00]
 [4.037e+03 2.840e+02 1.000e+00]
 [4.038e+03 3.310e+02 1.000e+00]
 [4.039e+03 2.990e+02 1.000e+00]
 [4.040e+03 2.930e+02 4.000e+00]
 [4.041e+03 3.460e+02 1.000e+00]
 [4.042e+03 2.940e+02 1.000e+00]
 [4.043e+03 2.890e+02 1.000e+00]
 [4.044e+03 3.450e+02 1.000e+00]
 [4.045e+03 3.060e+02 4.000e+00]
 [4.046e+03 3.340e+02 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0             350.0         1.0      1
1             332.5         4.5      2
2             370.0         1.0      2
3             291.5         1.0      2
4             331.0         1.0      1
[[4.047e+03 2.450e+02 5.000e+00]
 [4.048e+03 3.550e+02 1.000e+00]
 [4.049e+03 2.460e+02 5.000e+00]
 [4.050e+03 3.410e+02 1.000e+00]
 [4.051e+03 2.920e+02 5.000e+00]
 [4.052e+03 3.950e+02 1.000e+00]
 [4.053e+03 2.920e+02 5.000e+00]
 [4.054e+03 3.910e+02 1.000e+00]
 [4.05

[[4.314e+03 3.000e+01 7.000e+00]
 [4.315e+03 3.200e+01 7.000e+00]
 [4.316e+03 3.400e+01 5.000e+00]
 [4.317e+03 3.900e+01 2.000e+00]
 [4.318e+03 3.000e+01 7.000e+00]
 [4.319e+03 3.000e+01 7.000e+00]
 [4.320e+03 2.900e+01 2.000e+00]
 [4.321e+03 2.900e+01 2.000e+00]
 [4.322e+03 2.900e+01 3.000e+00]
 [4.323e+03 2.900e+01 2.000e+00]]
   Mean Consomption  Mean Hours  Count
0              32.0    6.333333      3
1              39.0    2.000000      1
2              30.0    7.000000      2
3              29.0    2.250000      4
[[4.324e+03 5.500e+01 1.000e+00]
 [4.325e+03 5.800e+01 1.000e+00]
 [4.326e+03 5.600e+01 1.000e+00]
 [4.327e+03 5.600e+01 1.000e+00]
 [4.328e+03 5.600e+01 2.000e+00]
 [4.329e+03 5.800e+01 1.000e+00]
 [4.330e+03 5.700e+01 4.000e+00]
 [4.331e+03 5.600e+01 1.000e+00]
 [4.332e+03 5.500e+01 2.000e+00]
 [4.333e+03 5.600e+01 5.000e+00]
 [4.334e+03 5.600e+01 5.000e+00]]
   Mean Consomption  Mean Hours  Count
0              56.5    1.166667      6
1              56.0    3.000000 

[[4.575e+03 1.000e+01 1.000e+00]
 [4.576e+03 9.000e+00 1.000e+00]
 [4.577e+03 9.000e+00 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0          9.333333         1.0      3
[[4.578e+03 1.700e+01 3.000e+00]
 [4.579e+03 3.700e+01 1.000e+00]
 [4.580e+03 1.800e+01 6.000e+00]
 [4.581e+03 3.700e+01 1.000e+00]
 [4.582e+03 1.800e+01 6.000e+00]
 [4.583e+03 3.700e+01 1.000e+00]
 [4.584e+03 3.100e+01 1.000e+00]
 [4.585e+03 1.800e+01 5.000e+00]
 [4.586e+03 3.400e+01 1.000e+00]
 [4.587e+03 1.700e+01 6.000e+00]
 [4.588e+03 3.200e+01 1.000e+00]
 [4.589e+03 3.000e+01 1.000e+00]
 [4.590e+03 1.700e+01 5.000e+00]
 [4.591e+03 4.000e+01 1.000e+00]
 [4.592e+03 1.700e+01 4.000e+00]]
   Mean Consomption  Mean Hours  Count
0             17.00         3.0      1
1             37.00         1.0      3
2             18.00         6.0      2
3             31.75         1.0      4
4             17.50         5.5      2
[[4.593e+03 5.700e+01 1.000e+00]
 [4.594e+03 5.600e+01 1.000e+00]
 [4.595e+03 5.500e+01 1.00

# Prétraitement des données et appel du modèle de machine learning (Random Forest) pour nuits.

In [15]:
data = df[["Talon surconso identifie", "impact", "NbrHeures", "NbrNuits", "Impact conso (kWh)", "% Surconso", "Période d'alerte"]]
data.head()

Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      60.0      15          1       1.0                15.0   
1                      60.0      13          7       3.0               273.0   
2                      65.0      22          1       1.0                22.0   
3                      60.0      16          7       4.0               448.0   
4                     120.0      49          6       2.0               588.0   

  % Surconso Période d'alerte  
0        33%             Nuit  
1        28%             Nuit  
2        48%             Nuit  
3        35%             Nuit  
4        70%             Nuit

In [16]:
print(data.dtypes)

Talon surconso identifie    float64
impact                        int64
NbrHeures                     int64
NbrNuits                    float64
Impact conso (kWh)          float64
% Surconso                   object
Période d'alerte             object
dtype: object


In [17]:
# Transformation de la colonne '% Surconso' en float
data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)

# Affichage du dataframe après la transformation
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\3833681290.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      60.0      15          1       1.0                15.0   
1                      60.0      13          7       3.0               273.0   
2                      65.0      22          1       1.0                22.0   
3                      60.0      16          7       4.0               448.0   
4                     120.0      49          6       2.0               588.0   

   % Surconso Période d'alerte  
0        0.33             Nuit  
1        0.28             Nuit  
2        0.48             Nuit  
3        0.35             Nuit  
4        0.70             Nuit

In [18]:
# Créer un dictionnaire de mapping
mapping = {"Nuit": 0, "Dim": 1, "Jour": 2, "Jour/nuit": 3, "Jour/Nuit": 3}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)

# Afficher les 20 premières lignes du DataFrame
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_4288\3054528154.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      60.0      15          1       1.0                15.0   
1                      60.0      13          7       3.0               273.0   
2                      65.0      22          1       1.0                22.0   
3                      60.0      16          7       4.0               448.0   
4                     120.0      49          6       2.0               588.0   

   % Surconso  Période d'alerte  
0        0.33                 0  
1        0.28                 0  
2        0.48                 0  
3        0.35                 0  
4        0.70                 0

In [19]:
# Faire des prédictions pour chaque ligne de la dataframe
predictions = loaded_model.predict(data)
df["Catégorie"] = predictions
# Créer un dictionnaire de mapping
mapping = {0: "Investigation en cours", 1: "Changement de comportement", 2: "Eclairage", 3: "Froid", 4: "CVC", 5:"Multi-usage"}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
df['Catégorie'] = df['Catégorie'].replace(mapping)

df.head(15)

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- NbrHeures
- NbrNuits
- Talon surconso identifie
- impact
Feature names seen at fit time, yet now missing:
- DP Surconso (kW)
- Nb d'heures
- Nb nuits/jours concernés
- Talon surconso identifié

  warnings.warn(message, FutureWarning)


Code      Energie  heure ouverture  heure fermetur  TalonRef  \
0    CS531  Electricité                4              20        45   
1    CS531  Electricité                4              20        45   
2    CS531  Electricité                4              20        45   
3    CS531  Electricité                4              20        45   
4   MO0160  Electricité                5              23        70   
5   MO0160  Electricité                5              23        70   
6   MO0160  Electricité                5              23        70   
7   MO0160  Electricité                5              23        70   
8   MO0160  Electricité                5              23        70   
9   MO0160  Electricité                5              23        70   
10  MO0102  Electricité                5              21        65   
11  MO0102  Electricité                5              21        65   
12  MO0102  Electricité                5              21        65   
13  MO0102  Electricité                5              21        65   
14  MO1244  Electricité                5              21        60   

   Début surconsommation Fin surconsommation  Talon surconso identifie  \
0             2024-01-21          2024-01-22                      60.0   
1             2024-01-21          2024-01-24                      60.0   
2             2024-01-24          2024-01-25                      65.0   
3             2024-01-24          2024-01-28                      60.0   
4             2024-01-21          2024-01-23                     120.0   
5             2024-01-23          2024-01-24                     105.0   
6             2024-01-24          2024-01-25                      90.0   
7             2024-01-24          2024-01-25                      80.0   
8             2024-01-26          2024-01-27                      90.0   
9             2024-01-27          2024-01-28                     105.0   
10            2024-01-21          2024-01-22                      80.0   
11            2024-01-22          2024-01-23                      70.0   
12            2024-01-22          2024-01-24                     100.0   
13            2024-01-23          2024-01-27                      90.0   
14            2024-01-22          2024-01-25                      70.0   

    impact  NbrHeures  NbrNuits  Impact conso (kWh) % Surconso  \
0       15          1       1.0                15.0        33%   
1       13          7       3.0               273.0        28%   
2       22          1       1.0                22.0        48%   
3       16          7       4.0               448.0        35%   
4       49          6       2.0               588.0        70%   
5       35          6       1.0               210.0        50%   
6       21          2       2.0                84.0        30%   
7        9          2       1.0                18.0        12%   
8       18          6       1.0               108.0        25%   
9       33          6       1.0               198.0        47%   
10      17          1       1.0                17.0        26%   
11       7          6       1.0                42.0        10%   
12      35          2       2.0               140.0        53%   
13      25          1       4.0               100.0        38%   
14       9          7       3.0               189.0        15%   

   Période d'alerte Pourcentage de précision                   Catégorie  \
0              Nuit                      70%                         CVC   
1              Nuit                      70%  Changement de comportement   
2              Nuit                      70%                         CVC   
3              Nuit                      70%  Changement de comportement   
4              Nuit                      50%  Changement de comportement   
5              Nuit                      50%  Changement de comportement   
6              Nuit                      50%                         CVC   
7              Nuit                

In [ ]:
df_ref = pd.read_excel('fichier2.xlsx', sheet_name='new BD horaires', header=0, skiprows=0)
print(df_ref.head())

In [ ]:
# Convertir les colonnes d'heure en objets datetime
df_ref['Horaire Ferm S'] = pd.to_datetime(df_ref['Horaire Ferm S'], format='%H:%M:%S')
df_ref['Horaire Ouv S'] = pd.to_datetime(df_ref['Horaire Ouv S'], format='%H:%M:%S')

# Créer la petite DataFrame df1
df1 = pd.DataFrame(columns=['Code', 'Durée Fermeture'])

# Boucler sur chaque site
for code_site in df['Code'].unique():
    # Filtrer les horaires de fermeture pour le site correspondant
    horaires_site = df_ref[df_ref['Code site'] == code_site]

    # Initialiser la durée de fermeture pour le site
    duree_fermeture = 0

    # Calculer la durée de fermeture pour chaque période
    for _, horaire_row in horaires_site.iterrows():
        fermeture = horaire_row['Horaire Ferm S']
        ouverture = horaire_row['Horaire Ouv S'] + pd.Timedelta(days=1)  # Ajouter 1 jour pour les fermetures de nuit
        duree_fermeture += round((ouverture - fermeture).seconds / 3600, 2)  # Convertir en heures avec deux décimales

    # Ajouter une ligne à la DataFrame df1
    df1.loc[len(df1)] = {'Code': code_site, 'Durée Fermeture': duree_fermeture}

# Fusionner les DataFrames sur la colonne 'Code site'
df = pd.merge(df, df1, how='left', on='Code')

# Afficher la DataFrame mise à jour
print(df.head(10))

In [20]:
df.to_excel(writer, sheet_name='Nuit', index=False)
print('---------------------------Sauvegarde---------------------------')
#writer.save()
writer.close()
print('---------------------------Fin analyse détection auto---------------------------')

---------------------------Sauvegarde---------------------------
---------------------------Fin analyse détection auto---------------------------


In [21]:
# import pandas as pd

# df_ref = pd.read_excel('fichier2 -012024.xlsx', sheet_name='S4', header=0, skiprows=0)
# df_ref.to_csv('S4.csv', index=False, encoding='utf-8-sig')